In [1]:
%matplotlib inline
import warnings
warnings.filterwarnings("ignore")

from sklearn.model_selection import train_test_split, KFold
import plotly.express as px
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import FunctionTransformer
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import PowerTransformer 
from sklearn.preprocessing import OrdinalEncoder, OneHotEncoder
from sklearn.feature_selection import SelectPercentile
from sklearn.model_selection import train_test_split, cross_val_score, cross_validate
from sklearn.metrics import mean_squared_error, f1_score
from sklearn import set_config
from lightgbm import LGBMRegressor
import lightgbm as lgb
import optuna
from optuna.distributions import CategoricalDistribution, IntDistribution, FloatDistribution
from optuna.integration import OptunaSearchCV, ShapleyImportanceEvaluator
from optuna.integration.lightgbm import LightGBMTunerCV #lgbm 전용 tunner 가 존재
from catboost import CatBoostRegressor
from sklearn.linear_model import Ridge
from sklearn.linear_model import RidgeClassifier
from sklearn.decomposition import PCA
from sklearn.linear_model import Lasso
from sklearn.metrics import mean_squared_error
from sklearn import model_selection
from category_encoders import TargetEncoder
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.tree import ExtraTreeClassifier
from catboost import CatBoostClassifier
from sklearn.cluster import KMeans

In [2]:
X_train = pd.read_csv('X_train_2.csv',encoding='cp949')
X_test = pd.read_csv('X_test_2.csv',encoding='cp949')
test = pd.read_csv('test.csv')
train = pd.read_csv('train.csv')
y_train = train['전화해지여부']

In [3]:
for df in [X_train, X_test]:
    numeric_features = df.dtypes[df.dtypes != "object"].index.tolist()
    print("Number of Numerical features: ", len(numeric_features))

Number of Numerical features:  22
Number of Numerical features:  22


In [4]:
def remove_outlier(X, q=0.05):  
    df = pd.DataFrame(X)
    return df.apply(lambda x: x.clip(x.quantile(q), x.quantile(1-q)), axis=0).values

numeric_transformer = Pipeline(
    steps=[
        ("imputer", SimpleImputer(strategy="median")),
        ("outlier", FunctionTransformer(remove_outlier, kw_args={'q':0.05})),
    ]
)


column_transformer = ColumnTransformer(
    transformers=[
        ("num", numeric_transformer, numeric_features),
    ]
)

preprocessor = Pipeline(
    steps=[
        ("column", column_transformer), 
    ]
)


set_config(display="diagram")  # To view the text pipeline, change to display='text'.
preprocessor

Pipeline(steps=[('column',
                 ColumnTransformer(transformers=[('num',
                                                  Pipeline(steps=[('imputer',
                                                                   SimpleImputer(strategy='median')),
                                                                  ('outlier',
                                                                   FunctionTransformer(func=<function remove_outlier at 0x00000266B48DFAF0>,
                                                                                       kw_args={'q': 0.05}))]),
                                                  ['가입일', '음성사서함이용', '주간통화시간',
                                                   '주간통화횟수', '주간통화요금', '저녁통화시간',
                                                   '저녁통화횟수', '저녁통화요금', '밤통화시간',
                                                   '밤통화횟수', '밤통화요금', '상담전화건수',
                                                   '가입월', '가입년', '총통화시간',
                                                   '총통화요금', '총통화횟수', '통화시간곱',
                                                   '통화요금곱', '통화횟수곱', '장기',
                                                   '상담+음성'])]))])

In [5]:
X_train = preprocessor.fit_transform(X_train, y_train)
X_test = preprocessor.transform(X_test)

In [6]:
from sklearn.preprocessing import StandardScaler, MinMaxScaler, MaxAbsScaler
scaler = MinMaxScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

In [168]:
# X = pd.DataFrame(X_train)
# Y = pd.DataFrame(y_train)
# Xt = pd.DataFrame(X_test)

In [169]:
# kmeans = KMeans(n_clusters=5, init='k-means++')
# kmeans.fit_transform(X,Y)
# kmeans.transform(Xt)

# pre_X5 = kmeans.predict(X)
# k_means_5 = pd.DataFrame(pre_X5)
# X['cluster5'] = k_means_5 


# pre_Xt5 = kmeans.predict(Xt)
# k_means_t5 = pd.DataFrame(pre_Xt5)
# Xt['cluster5'] = k_means_t5 

In [170]:
# kmeans10 = KMeans(n_clusters=10, init='k-means++')
# kmeans10.fit_transform(X,Y)
# kmeans10.transform(Xt)

# pre_X10 = kmeans10.predict(X)
# k_means_10 = pd.DataFrame(pre_X10)
# X['cluster10'] = k_means_10 

# pre_Xt10 = kmeans10.predict(Xt)
# k_means_t10 = pd.DataFrame(pre_Xt10)
# Xt['cluster10'] = k_means_t10 

In [171]:
# X_train = np.array(X)
# X_test = np.array(Xt)
# y_train = np.array(Y)

- 오히려 성능이 저하돼 주석처리

In [7]:
%%time

models = cross_validate(CatBoostClassifier(task_type = 'CPU',learning_rate=0.03,iterations=7000, verbose=True, random_state=0),
                        X_train, y_train, 
                        cv=10, 
                        scoring='accuracy', 
                        return_estimator=True)
oof_pred = np.array([m.predict(X_test) for m in models['estimator']]).mean(axis=0)

scores = models['test_score']
print("\nCatBoost CV scores: ", scores)
print("CatBoost CV mean = %.2f" % scores.mean(), "with std = %.2f" % scores.std())

0:	learn: 0.6684360	total: 216ms	remaining: 25m 13s
1:	learn: 0.6451930	total: 241ms	remaining: 14m 3s
2:	learn: 0.6241306	total: 261ms	remaining: 10m 8s
3:	learn: 0.6040972	total: 281ms	remaining: 8m 11s
4:	learn: 0.5846879	total: 299ms	remaining: 6m 58s
5:	learn: 0.5675824	total: 319ms	remaining: 6m 11s
6:	learn: 0.5507736	total: 335ms	remaining: 5m 34s
7:	learn: 0.5358512	total: 352ms	remaining: 5m 7s
8:	learn: 0.5223089	total: 368ms	remaining: 4m 46s
9:	learn: 0.5092140	total: 383ms	remaining: 4m 27s
10:	learn: 0.4974079	total: 399ms	remaining: 4m 13s
11:	learn: 0.4864029	total: 417ms	remaining: 4m 3s
12:	learn: 0.4762425	total: 438ms	remaining: 3m 55s
13:	learn: 0.4666467	total: 455ms	remaining: 3m 47s
14:	learn: 0.4578898	total: 474ms	remaining: 3m 40s
15:	learn: 0.4496824	total: 490ms	remaining: 3m 33s
16:	learn: 0.4415721	total: 506ms	remaining: 3m 27s
17:	learn: 0.4344459	total: 523ms	remaining: 3m 22s
18:	learn: 0.4277557	total: 540ms	remaining: 3m 18s
19:	learn: 0.4215034	to

158:	learn: 0.2989953	total: 3.04s	remaining: 2m 10s
159:	learn: 0.2987615	total: 3.06s	remaining: 2m 10s
160:	learn: 0.2984406	total: 3.08s	remaining: 2m 10s
161:	learn: 0.2982366	total: 3.1s	remaining: 2m 10s
162:	learn: 0.2980408	total: 3.12s	remaining: 2m 10s
163:	learn: 0.2978702	total: 3.14s	remaining: 2m 10s
164:	learn: 0.2977613	total: 3.15s	remaining: 2m 10s
165:	learn: 0.2976162	total: 3.17s	remaining: 2m 10s
166:	learn: 0.2974029	total: 3.19s	remaining: 2m 10s
167:	learn: 0.2972391	total: 3.21s	remaining: 2m 10s
168:	learn: 0.2968592	total: 3.23s	remaining: 2m 10s
169:	learn: 0.2967350	total: 3.25s	remaining: 2m 10s
170:	learn: 0.2965858	total: 3.27s	remaining: 2m 10s
171:	learn: 0.2964326	total: 3.29s	remaining: 2m 10s
172:	learn: 0.2962047	total: 3.31s	remaining: 2m 10s
173:	learn: 0.2960073	total: 3.33s	remaining: 2m 10s
174:	learn: 0.2958363	total: 3.35s	remaining: 2m 10s
175:	learn: 0.2956856	total: 3.37s	remaining: 2m 10s
176:	learn: 0.2954307	total: 3.39s	remaining: 2

321:	learn: 0.2702664	total: 6.09s	remaining: 2m 6s
322:	learn: 0.2701088	total: 6.11s	remaining: 2m 6s
323:	learn: 0.2699744	total: 6.13s	remaining: 2m 6s
324:	learn: 0.2698198	total: 6.15s	remaining: 2m 6s
325:	learn: 0.2696626	total: 6.16s	remaining: 2m 6s
326:	learn: 0.2694717	total: 6.19s	remaining: 2m 6s
327:	learn: 0.2692569	total: 6.2s	remaining: 2m 6s
328:	learn: 0.2690700	total: 6.22s	remaining: 2m 6s
329:	learn: 0.2688854	total: 6.24s	remaining: 2m 6s
330:	learn: 0.2687549	total: 6.26s	remaining: 2m 6s
331:	learn: 0.2686154	total: 6.28s	remaining: 2m 6s
332:	learn: 0.2684265	total: 6.3s	remaining: 2m 6s
333:	learn: 0.2682799	total: 6.32s	remaining: 2m 6s
334:	learn: 0.2679790	total: 6.34s	remaining: 2m 6s
335:	learn: 0.2677089	total: 6.36s	remaining: 2m 6s
336:	learn: 0.2675756	total: 6.38s	remaining: 2m 6s
337:	learn: 0.2674361	total: 6.39s	remaining: 2m 6s
338:	learn: 0.2672724	total: 6.41s	remaining: 2m 6s
339:	learn: 0.2671391	total: 6.43s	remaining: 2m 6s
340:	learn: 0.

485:	learn: 0.2450474	total: 9.15s	remaining: 2m 2s
486:	learn: 0.2449039	total: 9.17s	remaining: 2m 2s
487:	learn: 0.2447746	total: 9.19s	remaining: 2m 2s
488:	learn: 0.2446627	total: 9.21s	remaining: 2m 2s
489:	learn: 0.2445511	total: 9.22s	remaining: 2m 2s
490:	learn: 0.2444359	total: 9.24s	remaining: 2m 2s
491:	learn: 0.2442884	total: 9.26s	remaining: 2m 2s
492:	learn: 0.2441376	total: 9.27s	remaining: 2m 2s
493:	learn: 0.2440294	total: 9.29s	remaining: 2m 2s
494:	learn: 0.2438736	total: 9.31s	remaining: 2m 2s
495:	learn: 0.2437629	total: 9.32s	remaining: 2m 2s
496:	learn: 0.2435965	total: 9.34s	remaining: 2m 2s
497:	learn: 0.2434260	total: 9.36s	remaining: 2m 2s
498:	learn: 0.2432683	total: 9.37s	remaining: 2m 2s
499:	learn: 0.2431648	total: 9.39s	remaining: 2m 2s
500:	learn: 0.2430194	total: 9.41s	remaining: 2m 2s
501:	learn: 0.2428904	total: 9.43s	remaining: 2m 2s
502:	learn: 0.2427810	total: 9.44s	remaining: 2m 1s
503:	learn: 0.2425698	total: 9.46s	remaining: 2m 1s
504:	learn: 

643:	learn: 0.2256401	total: 12s	remaining: 1m 58s
644:	learn: 0.2255375	total: 12s	remaining: 1m 58s
645:	learn: 0.2253829	total: 12s	remaining: 1m 58s
646:	learn: 0.2252682	total: 12s	remaining: 1m 58s
647:	learn: 0.2251075	total: 12s	remaining: 1m 58s
648:	learn: 0.2249865	total: 12.1s	remaining: 1m 58s
649:	learn: 0.2248696	total: 12.1s	remaining: 1m 57s
650:	learn: 0.2246605	total: 12.1s	remaining: 1m 57s
651:	learn: 0.2245413	total: 12.1s	remaining: 1m 57s
652:	learn: 0.2243859	total: 12.1s	remaining: 1m 57s
653:	learn: 0.2242545	total: 12.1s	remaining: 1m 57s
654:	learn: 0.2241548	total: 12.2s	remaining: 1m 57s
655:	learn: 0.2240445	total: 12.2s	remaining: 1m 57s
656:	learn: 0.2239559	total: 12.2s	remaining: 1m 57s
657:	learn: 0.2237933	total: 12.2s	remaining: 1m 57s
658:	learn: 0.2236942	total: 12.2s	remaining: 1m 57s
659:	learn: 0.2235997	total: 12.2s	remaining: 1m 57s
660:	learn: 0.2235192	total: 12.3s	remaining: 1m 57s
661:	learn: 0.2233448	total: 12.3s	remaining: 1m 57s
662

...

6276:	learn: 0.0538133	total: 1m 58s	remaining: 13.7s
6277:	learn: 0.0538031	total: 1m 58s	remaining: 13.7s
6278:	learn: 0.0537934	total: 1m 58s	remaining: 13.6s
6279:	learn: 0.0537881	total: 1m 58s	remaining: 13.6s
6280:	learn: 0.0537806	total: 1m 58s	remaining: 13.6s
6281:	learn: 0.0537726	total: 1m 58s	remaining: 13.6s
6282:	learn: 0.0537635	total: 1m 58s	remaining: 13.6s
6283:	learn: 0.0537585	total: 1m 58s	remaining: 13.5s
6284:	learn: 0.0537456	total: 1m 58s	remaining: 13.5s
6285:	learn: 0.0537363	total: 1m 58s	remaining: 13.5s
6286:	learn: 0.0537291	total: 1m 58s	remaining: 13.5s
6287:	learn: 0.0537186	total: 1m 58s	remaining: 13.5s
6288:	learn: 0.0537087	total: 1m 58s	remaining: 13.4s
6289:	learn: 0.0536982	total: 1m 58s	remaining: 13.4s
6290:	learn: 0.0536856	total: 1m 58s	remaining: 13.4s
6291:	learn: 0.0536750	total: 1m 58s	remaining: 13.4s
6292:	learn: 0.0536606	total: 1m 58s	remaining: 13.4s
6293:	learn: 0.0536588	total: 1m 59s	remaining: 13.3s
6294:	learn: 0.0536557	total

6442:	learn: 0.0523351	total: 2m 1s	remaining: 10.5s
6443:	learn: 0.0523287	total: 2m 1s	remaining: 10.5s
6444:	learn: 0.0523242	total: 2m 1s	remaining: 10.5s
6445:	learn: 0.0523192	total: 2m 1s	remaining: 10.5s
6446:	learn: 0.0523132	total: 2m 1s	remaining: 10.5s
6447:	learn: 0.0523071	total: 2m 1s	remaining: 10.4s
6448:	learn: 0.0522955	total: 2m 1s	remaining: 10.4s
6449:	learn: 0.0522885	total: 2m 1s	remaining: 10.4s
6450:	learn: 0.0522794	total: 2m 1s	remaining: 10.4s
6451:	learn: 0.0522707	total: 2m 1s	remaining: 10.4s
6452:	learn: 0.0522598	total: 2m 1s	remaining: 10.3s
6453:	learn: 0.0522543	total: 2m 1s	remaining: 10.3s
6454:	learn: 0.0522458	total: 2m 2s	remaining: 10.3s
6455:	learn: 0.0522370	total: 2m 2s	remaining: 10.3s
6456:	learn: 0.0522245	total: 2m 2s	remaining: 10.3s
6457:	learn: 0.0522142	total: 2m 2s	remaining: 10.2s
6458:	learn: 0.0522037	total: 2m 2s	remaining: 10.2s
6459:	learn: 0.0521978	total: 2m 2s	remaining: 10.2s
6460:	learn: 0.0521911	total: 2m 2s	remaining:

6599:	learn: 0.0509528	total: 2m 4s	remaining: 7.56s
6600:	learn: 0.0509445	total: 2m 4s	remaining: 7.54s
6601:	learn: 0.0509353	total: 2m 4s	remaining: 7.52s
6602:	learn: 0.0509309	total: 2m 4s	remaining: 7.51s
6603:	learn: 0.0509209	total: 2m 4s	remaining: 7.49s
6604:	learn: 0.0509178	total: 2m 4s	remaining: 7.47s
6605:	learn: 0.0509080	total: 2m 4s	remaining: 7.45s
6606:	learn: 0.0508997	total: 2m 4s	remaining: 7.43s
6607:	learn: 0.0508907	total: 2m 4s	remaining: 7.41s
6608:	learn: 0.0508843	total: 2m 4s	remaining: 7.39s
6609:	learn: 0.0508743	total: 2m 4s	remaining: 7.37s
6610:	learn: 0.0508676	total: 2m 4s	remaining: 7.35s
6611:	learn: 0.0508609	total: 2m 5s	remaining: 7.33s
6612:	learn: 0.0508538	total: 2m 5s	remaining: 7.32s
6613:	learn: 0.0508390	total: 2m 5s	remaining: 7.3s
6614:	learn: 0.0508335	total: 2m 5s	remaining: 7.28s
6615:	learn: 0.0508216	total: 2m 5s	remaining: 7.26s
6616:	learn: 0.0508103	total: 2m 5s	remaining: 7.24s
6617:	learn: 0.0507995	total: 2m 5s	remaining: 

6761:	learn: 0.0495389	total: 2m 7s	remaining: 4.5s
6762:	learn: 0.0495320	total: 2m 7s	remaining: 4.48s
6763:	learn: 0.0495279	total: 2m 7s	remaining: 4.46s
6764:	learn: 0.0495195	total: 2m 7s	remaining: 4.44s
6765:	learn: 0.0495120	total: 2m 7s	remaining: 4.42s
6766:	learn: 0.0495018	total: 2m 7s	remaining: 4.4s
6767:	learn: 0.0494939	total: 2m 7s	remaining: 4.38s
6768:	learn: 0.0494886	total: 2m 7s	remaining: 4.37s
6769:	learn: 0.0494779	total: 2m 7s	remaining: 4.35s
6770:	learn: 0.0494736	total: 2m 7s	remaining: 4.33s
6771:	learn: 0.0494674	total: 2m 7s	remaining: 4.31s
6772:	learn: 0.0494608	total: 2m 8s	remaining: 4.29s
6773:	learn: 0.0494519	total: 2m 8s	remaining: 4.27s
6774:	learn: 0.0494444	total: 2m 8s	remaining: 4.25s
6775:	learn: 0.0494359	total: 2m 8s	remaining: 4.23s
6776:	learn: 0.0494262	total: 2m 8s	remaining: 4.21s
6777:	learn: 0.0494158	total: 2m 8s	remaining: 4.2s
6778:	learn: 0.0494059	total: 2m 8s	remaining: 4.18s
6779:	learn: 0.0493993	total: 2m 8s	remaining: 4.

6920:	learn: 0.0483191	total: 2m 10s	remaining: 1.49s
6921:	learn: 0.0483095	total: 2m 10s	remaining: 1.47s
6922:	learn: 0.0483035	total: 2m 10s	remaining: 1.46s
6923:	learn: 0.0482987	total: 2m 10s	remaining: 1.44s
6924:	learn: 0.0482965	total: 2m 10s	remaining: 1.42s
6925:	learn: 0.0482838	total: 2m 10s	remaining: 1.4s
6926:	learn: 0.0482725	total: 2m 10s	remaining: 1.38s
6927:	learn: 0.0482677	total: 2m 10s	remaining: 1.36s
6928:	learn: 0.0482625	total: 2m 11s	remaining: 1.34s
6929:	learn: 0.0482541	total: 2m 11s	remaining: 1.32s
6930:	learn: 0.0482488	total: 2m 11s	remaining: 1.3s
6931:	learn: 0.0482398	total: 2m 11s	remaining: 1.28s
6932:	learn: 0.0482328	total: 2m 11s	remaining: 1.27s
6933:	learn: 0.0482230	total: 2m 11s	remaining: 1.25s
6934:	learn: 0.0482204	total: 2m 11s	remaining: 1.23s
6935:	learn: 0.0482147	total: 2m 11s	remaining: 1.21s
6936:	learn: 0.0482085	total: 2m 11s	remaining: 1.19s
6937:	learn: 0.0482006	total: 2m 11s	remaining: 1.17s
6938:	learn: 0.0481945	total: 

In [8]:
# Voting
from collections import Counter
a = []
for j in [i.predict(X_test) for i in models['estimator']]:
    a.append(j.tolist())
    
grouped_values = zip(*a)
mode_values = []
for group in grouped_values:
    mode_values.append(Counter(group).most_common(1)[0][0])

In [9]:
filename = 'final_sub.csv'
pd.DataFrame({'ID':test['ID'], '전화해지여부':mode_values}).to_csv(filename, index=False)